# Elastic search query

In [ ]:
import requests
import json
from elasticsearch import Elasticsearch
import pandas as pd
import os
import numpy as np
import dateutil

Just replace servername by the name of the server where the elastic search is running

In [ ]:
es = Elasticsearch('http://servername:9200', timeout=20.0, bulk_size=100000)

# Basic request

## Default size

In [4]:
results = es.search(index="asm", doc_type="dimm")
print("{0:d} documents found".format(results['hits']['total']))

156459 documents found


The result of the search is a dictionary with 4 keys:

In [5]:
print(results.keys())

dict_keys(['_shards', 'hits', 'took', 'timed_out'])


In [6]:
results['took']

4

In [7]:
results['timed_out']

False

In [50]:
results['_shards']

{'failed': 0, 'successful': 5, 'total': 5}

The hits is itself a dictionnary with different keys: total, max_score and hits

In [51]:
print(results['hits'].keys())
print(len(results['hits']['hits']))
#print(results['hits'])

dict_keys(['total', 'max_score', 'hits'])
10


If we look at one of those hits:

In [52]:
i=2
print(results['hits']['hits'][i])
print(results['hits']['hits'][i]['_source'])

{'_id': 'AVxGFXJkj_k52QMFZJII', '_type': 'dimm', '_index': 'asm', '_score': 1.0, '_source': {'@timestamp': '2017-04-28T03:43:16', 'dimm_seeing': 0.527}}
{'@timestamp': '2017-04-28T03:43:16', 'dimm_seeing': 0.527}


We can turn that into a dataframe

In [53]:
feList={'timestamp':[],'dimm_seeing':[]}
for r in results['hits']['hits']:
    feList['timestamp'].append(dateutil.parser.parse(r['_source']['@timestamp'], ignoretz=True))
    feList['dimm_seeing'].append(r['_source']['dimm_seeing'])

# Create a Dataframe with the data retrieved
fe_dt = pd.DataFrame(feList['dimm_seeing'], index=feList['timestamp'], columns=['dimm_seeing'])

In [54]:
print(len(fe_dt))
fe_dt.head()

10


dimm_seeing
2017-04-28 03:36:57        0.542
2017-04-28 03:41:57        0.570
2017-04-28 03:43:16        0.527
2017-04-28 03:58:23        0.454
2017-04-28 04:03:35        0.439

## Increased size

We saw before that the default size returns only 10 hits. Let's increase that to 1000 and loop over the search to get all possible hits.

In [42]:
feList = { 'timestamp': [], 'dimm_seeing': []}

# Initialize the scroll
results = es.search(index = 'asm',doc_type = 'dimm',scroll = '2m',size = 1000)
for r in results['hits']['hits']:
    feList['timestamp'].append(dateutil.parser.parse(r['_source']['@timestamp'], ignoretz=True))
    feList['dimm_seeing'].append(r['_source']['dimm_seeing'])

sid = results['_scroll_id']
scroll_size = results['hits']['total']
total=scroll_size
# Start scrolling
while (scroll_size > 0):
    print("Scrolling...")
    results = es.scroll(scroll_id = sid, scroll = '2m')
    # Update the scroll ID
    sid = results['_scroll_id']
    # Get the number of results that we returned in the last scroll
    scroll_size = len(results['hits']['hits'])
    print("scroll size: {0:d}".format(scroll_size))
    # Do something with the obtained page
    for r in results['hits']['hits']:
        feList['timestamp'].append(dateutil.parser.parse(r['_source']['@timestamp'], ignoretz=True))
        feList['dimm_seeing'].append(r['_source']['dimm_seeing'])
    total+=scroll_size
print(total)

Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrolling...
scroll size: 1000
Scrollin

In [55]:
# Create a Dataframe with the data retrieved
fe_dt = pd.DataFrame(feList['dimm_seeing'], index=feList['timestamp'], columns=['dimm_seeing'])
print(len(fe_dt))
fe_dt.head()

10


dimm_seeing
2017-04-28 03:36:57        0.542
2017-04-28 03:41:57        0.570
2017-04-28 03:43:16        0.527
2017-04-28 03:58:23        0.454
2017-04-28 04:03:35        0.439

# Advanced request

## First trial using es.search

In [15]:
query={
  "size": 0,
  "query": {
    "bool": {
      "must": [
        {
          "query_string": {
            "analyze_wildcard": True,
            "query": "*"
          }
        },
        {
          "range": {
            "@timestamp": {
              "gte": 1432666102379,
              "lte": 1495828102379,
              "format": "epoch_millis"
            }
          }
        }
      ],
      "must_not": []
    }
  },
  "_source": {
    "excludes": []
  },
  "aggs": {
    "2": {
      "date_histogram": {
        "field": "@timestamp",
        "interval": "1w",
        "time_zone": "America/Santiago",
        "min_doc_count": 1
      },
      "aggs": {
        "1": {
          "avg": {
            "field": "dimm_seeing"
          }
        }
      }
    }
  }
}
results = es.search(index="asm", body=query)
print("{0:d} documents found".format(results['hits']['total']))

458763 documents found


In [16]:
feList = { 'timestamp': [], 'dimm_seeing': []}
keep_fetching = True

count = 0
while keep_fetching:
    i = 0
    for r in results['hits']['hits']:
        feList['timestamp'].append(dateutil.parser.parse(r['_source']['@timestamp'], ignoretz=True))
        feList['dimm_seeing'].append(r['_source']['dimm_seeing'])
        i += 1

    if i == 10000:
        count += i
        #print (count, "mark...")
        uri = 'http://134.171.189.13:9200/_search/scroll'
        esBody = """
        {{
            "scroll": "1m",
            "scroll_id": "{}"
        }}
        """.format(results['_scroll_id'])
        response = requests.post(uri, esBody)
        results = json.loads(response.text)
    else:
        keep_fetching = False

# Create a Dataframe with the data retrieved
fe_dt = pd.DataFrame(feList['dimm_seeing'], index=feList['timestamp'], columns=['dimm_seeing'])
fe_dt['occurrence'] = np.ones(len(fe_dt), dtype=int)



In [19]:
results['hits']

{'hits': [], 'max_score': 0.0, 'total': 458763}

## Second trial using json

In [ ]:
# Fetching from ES
# The data will be retrieved in batches of 10k records 
# Only fields requested are the timestamp and dimm_seeing
esBody = """
{
    "_source": ["@timestamp", "dimm_seeing"],
    "sort" : {
        "@timestamp": {"order": "asc"}
    },
    "query" :{
        "query_string" : {
            "query": @timestamp:[2016-01-01 TO now]"
        }
    }
    ,"size": 10000
}
"""
uri = 'http://134.171.189.13:9200/asm/_search?scroll=1m'
response = requests.post(uri, esBody)
results = json.loads(response.text)

feList = { 'timestamp': [], 'dimm_seeing': []}
keep_fetching = True

count = 0
while keep_fetching:
    i = 0
    for r in results['hits']['hits']:
        feList['timestamp'].append(dateutil.parser.parse(r['_source']['@timestamp'], ignoretz=True))
        feList['dimm_seeing'].append(r['_source']['dimm_seeing'])
        i += 1

    if i == 10000:
        count += i
        #print (count, "mark...")
        uri = 'http://134.171.189.13:9200/_search/scroll'
        esBody = """
        {{
            "scroll": "1m",
            "scroll_id": "{}"
        }}
        """.format(results['_scroll_id'])
        response = requests.post(uri, esBody)
        results = json.loads(response.text)
    else:
        keep_fetching = False

# Create a Dataframe with the data retrieved
fe_dt = pd.DataFrame(feList['dimm_seeing'], index=feList['timestamp'], columns=['dimm_seeing'])
fe_dt['occurrence'] = np.ones(len(fe_dt), dtype=int)

del(feList)
del(response)
del(results)